In [1]:
import pickle
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
import itertools
import numpy as np

%matplotlib inline

In [2]:
def get_simmat(model1_details, model2_details):

    model1_name, model1_mode = model1_details
    model2_name, model2_mode = model2_details
    
    folder = "sim_mat/"
    file_name = folder + 'sim_mat_' + model1_name + '_' + model1_mode + '_' + model2_name + '_' + model2_mode + '.pkl'

    with open(file_name, 'rb') as f:
            sim_mat = pickle.load(f)
            print(file_name+' read')
    return sim_mat

In [3]:
names = ['MoCo-V3', 'DINO', 'MAE']
modes = ['pretrained']
sim_mats = {}

prod = list(itertools.product(names, modes))
combs = list(itertools.combinations(prod, 2))
for comb in combs:
    print(comb)
    sim_mats[comb] = get_simmat(*comb)    

(('MoCo-V3', 'pretrained'), ('DINO', 'pretrained'))
sim_mat/sim_mat_MoCo-V3_pretrained_DINO_pretrained.pkl read
(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
sim_mat/sim_mat_MoCo-V3_pretrained_MAE_pretrained.pkl read
(('DINO', 'pretrained'), ('MAE', 'pretrained'))
sim_mat/sim_mat_DINO_pretrained_MAE_pretrained.pkl read


In [4]:
fig_dir = "/private/home/sshkhr/mae/figures/ICML/"

In [5]:
fig, axn = plt.subplots(1, 3, figsize=(28, 11), dpi=500, sharex=True, sharey=True)
cbar_ax = fig.add_axes([.9, .3, .01, .5])

sns.set(font_scale=1.5)

for i, ax in enumerate(axn.flat):
    print(combs[i])
    sns.heatmap(sim_mats[combs[i]], ax=ax,
                cbar=i == 0,
                vmin=0, vmax=1,
                cbar_ax=None if i else cbar_ax,
                cbar_kws={'label': 'CKA similarity', "ticks":[0,1]}, 
                annot_kws={'fontweight':"bold", "fontsize":20})
    ax.invert_yaxis()
    model1 = str(combs[i][0][0]) + " (PT)" + ' layers'
    model2 = str(combs[i][1][0]) + " (PT)" + ' layers'
    ax.set_ylabel(model1, fontweight="bold", fontsize = 40)
    ax.set_xlabel(model2, fontweight="bold", fontsize = 40)

    letter = {0:'(A) ', 1:'(B) ', 2:'(C) '}
    ax.set_title(letter[i]+combs[i][0][0]+" vs "+combs[i][1][0], fontdict={'fontweight':"bold", 'fontsize':40}, y=-0.35)

    ax.set_xticks(np.arange(0, 110, 20), visible=True)
    ax.set_yticks(np.arange(0, 110, 20), visible=True)
    ax.set_xticklabels([x for x in np.arange(0, 110, 20)], fontsize = 30)
    ax.set_yticklabels([x for x in np.arange(0, 110, 20)], fontsize = 30)
    
fig.tight_layout(rect=[0, 0, .9, 1])
cbar_ax.yaxis.label.set_size(30)
cbar_ax.yaxis.label.set_fontweight('bold')
cbar_ax.tick_params(labelsize=30)
cbar_ax.tick_params(size=0)

plt.show()

fig.savefig(fig_dir + 'CKA_pretrained.pdf', dpi=500, bbox_inches = "tight")


(('MoCo-V3', 'pretrained'), ('DINO', 'pretrained'))
(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
(('DINO', 'pretrained'), ('MAE', 'pretrained'))


/tmp/ipykernel_887929/1651457902.py:28: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  fig.tight_layout(rect=[0, 0, .9, 1])


In [6]:
layer_split = {'normalization': list(range(0, 108, 9)) + list(range(4, 108 ,9)),
                    'attention': list(range(1, 108, 9)) + list(range(2, 108 ,9)) + list(range(3, 108 ,9)),
                    'mlp_layers': list(range(5, 108, 9)) + list(range(6, 108 ,9)) + list(range(7, 108 ,9)) + list(range(8, 108 ,9)),
                    'norm-1': list(range(0, 108, 9)),
                    'attn':  list(range(1, 108, 9)),
                    'attn_qkv': list(range(2, 108, 9)),
                    'attn_proj': list(range(3, 108, 9)),
                    'norm-2': list(range(4, 108, 9)),
                    'mlp': list(range(5, 108, 9)),
                    'mlp_fc1': list(range(6, 108, 9)),
                    'mlp_act': list(range(7, 108, 9)),
                    'mlp_fc2': list(range(8, 108, 9)),
                }

In [7]:
indexes = ['norm-1', 'attn_qkv', 'mlp_fc1']

In [8]:
fig, axn = plt.subplots(1, 3, figsize=(28, 11), dpi=500, sharex=True, sharey=True)
cbar_ax = fig.add_axes([.9, .3, .01, .5])

sns.set(font_scale=1.5)

for i, ax in enumerate(axn.flat):
    print(combs[1])
    print(indexes[i])
    if indexes is not None:
        sim_mat = sim_mats[combs[1]][layer_split[indexes[i]], :][:, layer_split[indexes[i]]]
    ticklabels = [x for x in np.arange(1, 13, 1)]
    sns.heatmap(sim_mat, ax=ax,
                cbar=i == 0,
                vmin=0, vmax=1,
                xticklabels=ticklabels, 
                yticklabels=ticklabels,
                cbar_ax=None if i else cbar_ax,
                cbar_kws={'label': 'CKA similarity', 'ticks':[0,1]})
    ax.invert_yaxis()
    letter = {0:'(A) ', 1:'(B) ', 2:'(C) '}
    layer_names = {'norm-1':"Layer Norm", "attn_qkv":"Multi-Head Self-Attention", "mlp_fc1":"Fully-Connected"}
    ax.set_title(letter[i]+layer_names[indexes[i]], fontdict={'fontweight':"bold", 'fontsize':40}, y=-0.27)
    layer_name = indexes[i].upper().replace('_','-')
    model1 = str(combs[1][0][0]) + " (PT)" + ' layers'
    model2 = str(combs[1][1][0]) + " (PT)" + ' layers'
    ax.set_ylabel(model1, fontweight="bold", fontsize = 40)
    ax.set_xlabel(model2, fontweight="bold", fontsize = 40)

    ax.set_xticks(np.arange(0, 13, 2), visible=True)
    ax.set_yticks(np.arange(0, 13, 2), visible=True)
    ax.set_xticklabels([x for x in np.arange(0, 13, 2)], fontsize = 30)
    ax.set_yticklabels([x for x in np.arange(0, 13, 2)], fontsize = 30)
    
fig.tight_layout(rect=[0, 0, .9, 1])
cbar_ax.yaxis.label.set_size(30)
cbar_ax.yaxis.label.set_fontweight('bold')
cbar_ax.tick_params(labelsize=30)
cbar_ax.tick_params(size=0)

plt.show()

fig.savefig(fig_dir + 'CKA_layerwise.pdf', dpi=500, bbox_inches = "tight")


(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
norm-1
(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
attn_qkv
(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
mlp_fc1


/tmp/ipykernel_887929/4168975676.py:34: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  fig.tight_layout(rect=[0, 0, .9, 1])


In [9]:
names = [('MoCo-V3','pretrained'), ('MoCo-V3','finetuned')]
modes = [('MAE','pretrained'), ('MAE','finetuned')]
sim_mats = {}

combs = list(itertools.product(names, modes))
for comb in combs:
    print(comb)
    sim_mats[comb] = get_simmat(*comb)    

(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
sim_mat/sim_mat_MoCo-V3_pretrained_MAE_pretrained.pkl read
(('MoCo-V3', 'pretrained'), ('MAE', 'finetuned'))
sim_mat/sim_mat_MoCo-V3_pretrained_MAE_finetuned.pkl read
(('MoCo-V3', 'finetuned'), ('MAE', 'pretrained'))
sim_mat/sim_mat_MoCo-V3_finetuned_MAE_pretrained.pkl read
(('MoCo-V3', 'finetuned'), ('MAE', 'finetuned'))
sim_mat/sim_mat_MoCo-V3_finetuned_MAE_finetuned.pkl read


In [10]:
fig, axn = plt.subplots(2, 2, figsize=(30, 25), dpi=500, sharex=True, sharey=True)
cbar_ax = fig.add_axes([.9, .3, .01, .25])

sns.set(font_scale=1.5)

for i, ax in enumerate(axn.flat):
    print(combs[i])
    sns.heatmap(sim_mats[combs[i]], ax=ax,
                cbar=i == 0,
                vmin=0, vmax=1,
                cbar_ax=None if i else cbar_ax,
                cbar_kws={'label': 'CKA similarity', "ticks":[0,1]})
    ax.invert_yaxis()
    mode1 = 'PT' if combs[i][0][1]=='pretrained' else 'FT'
    mode2 = 'PT' if combs[i][1][1]=='pretrained' else 'FT'
    model1 = str(combs[i][0][0]) + " (" + mode1 + ")" + ' layers'
    model2 = str(combs[i][1][0]) + " (" + mode2 + ")" + ' layers'
    ax.set_ylabel(model1, fontweight="bold", fontsize = 60)
    ax.set_xlabel(model2, fontweight="bold", fontsize = 60)

    ax.set_xticks(np.arange(0, 110, 20), visible=True)
    ax.set_yticks(np.arange(0, 110, 20), visible=True)
    ax.set_xticklabels([x for x in np.arange(0, 110, 20)], fontsize = 50)
    ax.set_yticklabels([x for x in np.arange(0, 110, 20)], fontsize = 50)
    
fig.tight_layout(rect=[0, 0, .9, 1])
cbar_ax.yaxis.label.set_size(50)
cbar_ax.yaxis.label.set_fontweight('bold')
cbar_ax.tick_params(labelsize=50)
cbar_ax.tick_params(size=0)

plt.show()

fig.savefig(fig_dir + 'CKA_PT_FT.pdf', dpi=500, bbox_inches = "tight")


(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
(('MoCo-V3', 'pretrained'), ('MAE', 'finetuned'))
(('MoCo-V3', 'finetuned'), ('MAE', 'pretrained'))
(('MoCo-V3', 'finetuned'), ('MAE', 'finetuned'))


/tmp/ipykernel_887929/1542750274.py:26: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  fig.tight_layout(rect=[0, 0, .9, 1])


In [11]:
names = [('MoCo-V3','pretrained'), ('MoCo-V3','finetuned')]
modes = [('MAE','pretrained'), ('MAE','finetuned')]
sim_mats = {}

combs = list(itertools.product(names, modes))
for comb in combs:
    print(comb)
    sim_mats[comb] = get_simmat(*comb)    

(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
sim_mat/sim_mat_MoCo-V3_pretrained_MAE_pretrained.pkl read
(('MoCo-V3', 'pretrained'), ('MAE', 'finetuned'))
sim_mat/sim_mat_MoCo-V3_pretrained_MAE_finetuned.pkl read
(('MoCo-V3', 'finetuned'), ('MAE', 'pretrained'))
sim_mat/sim_mat_MoCo-V3_finetuned_MAE_pretrained.pkl read
(('MoCo-V3', 'finetuned'), ('MAE', 'finetuned'))
sim_mat/sim_mat_MoCo-V3_finetuned_MAE_finetuned.pkl read


In [12]:
indexes = ['attn_qkv']

In [14]:
fig, axn = plt.subplots(1, 3, figsize=(28, 11), dpi=500, sharex=True, sharey=True)
cbar_ax = fig.add_axes([.9, .3, .01, .5])

sns.set(font_scale=1.5)

for i, ax in enumerate(axn.flat):
    
    if (i==2):
        i = 3 #hack to access index 3 when not 0

    print(combs[i])
    if indexes is not None:
        sim_mat = sim_mats[combs[i]][layer_split[indexes[0]], :][:, layer_split[indexes[0]]]
    ticklabels = [x for x in np.arange(1, 13, 1)]
    sns.heatmap(sim_mat, ax=ax,
                cbar=i == 0,
                vmin=0, vmax=1,
                xticklabels=ticklabels, 
                yticklabels=ticklabels,
                cbar_ax=None if i else cbar_ax,
                cbar_kws={'label': 'CKA similarity', 'ticks':[0,1]})
    ax.invert_yaxis()
    layer_name = indexes[0].upper().replace('_','-')
    if str((combs[i][0][1])) == "finetuned":
        mode = 'FT'
        mode1 = mode
    else:
        mode = 'PT'
        mode1 = mode if str((combs[i][1][1])) != "finetuned" else 'FT'

    model1 = str(combs[i][0][0]) + " (" + mode + ")"# + " " + 'Attention' + ' layers'
    model2 = str(combs[i][1][0]) + " (" + mode1 + ")"# + " " + 'Attention' + ' layers'
    ax.set_ylabel(model1, fontweight="bold", fontsize = 40)
    ax.set_xlabel(model2, fontweight="bold", fontsize = 40)

    ax.set_xticks(np.arange(0, 13, 2), visible=True)
    ax.set_yticks(np.arange(0, 13, 2), visible=True)
    ax.set_xticklabels([x for x in np.arange(0, 13, 2)], fontsize = 40)
    ax.set_yticklabels([x for x in np.arange(0, 13, 2)], fontsize = 40)

fig.tight_layout(rect=[0, 0, .9, 1])
cbar_ax.yaxis.label.set_size(40)
cbar_ax.yaxis.label.set_fontweight('bold')
cbar_ax.tick_params(labelsize=40)
cbar_ax.tick_params(size=0)

plt.show()

fig.savefig(fig_dir + 'CKA_attn_PT_FT.pdf', dpi=500, bbox_inches = "tight")


(('MoCo-V3', 'pretrained'), ('MAE', 'pretrained'))
(('MoCo-V3', 'pretrained'), ('MAE', 'finetuned'))
(('MoCo-V3', 'finetuned'), ('MAE', 'finetuned'))


/tmp/ipykernel_887929/829709697.py:41: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  fig.tight_layout(rect=[0, 0, .9, 1])
